# Sensitivity Analysis

In this tutorial we demonstrate how to perform sensitivity analysis as part of the `AutoEmulate` workflow. The tutorial covers:

1. Setting up an example simulation: here we use our "FlowProblem" simulator. This is a cardiovascular modelling example, simulating a blood vessel divided into 10 compartments. This allows for the study of the pressure and flow rate at various points in the tube. See "The Flow Problem" below for more details.
2. Running the simulation for 100 sets of parameters sampled from the parameter space.
3. Using Autoemulate to find the best emulator for this simulation
4. Performing sensitivity analysis.

<details>
<summary>The Flow Problem</summary>

In the field of cardiovascular modeling, capturing the dynamics of blood flow and the associated pressures and volumes within the vascular system is crucial for understanding heart function and disease. This simulator simulates a vessel divided to 10 compartments.

### Parameters

The simulation parameters include :

1. R (Resistance):
   Represents the resistance to blood flow in blood vessels, akin to the hydraulic resistance caused by vessel diameter and blood viscosity (Analogous to electrical resistor).
2. L (Inductance):
   Represents the inertial effects of blood flow, capturing how blood resists changes in its velocity (Analogous to electrical inductor).
3. C (Capacitance):
   Represents the compliance or elasticity of blood vessels, primarily large arteries, which store and release blood volume with changes in pressure (Analogous to a capacitor).

### Boundary conditions

1. Neumann boundary condition : Specifies the derivative of the variable at the boundary.
2. Dirichlet Boundary condition : Specifies the value of the variable directly at the boundary.

### The setup

The input flow rate in each compartment is $Q_i(t)$ for the $i^{th}$ compartment and the output flow rate is $Q_{i+1}(t)$.

$Q_0(t) = 
\begin{cases} 
A \cdot \sin^2\left(\frac{\pi}{t_d} t\right), & \text{if } 0 \leq t < T, \\
0, & \text{otherwise}.
\end{cases}$

Where:

- $Q_0(t)$ is the input pulse function (flow rate) at time t
- A is the amplitude of the pulse
- $t_d$ is the pulse duration.

### Solve

Pressure in Each Compartment ($P_i$): This determines how the pressure in each compartment evolves over time, based on the inflow ($Q_i(t)$) and the outflow ($Q_{i+1}(t)$). where $i$ is the number of compartment.

<img src="../../../../misc/circuit.jpg" alt="Circuit Diagram" style="width:60%;"/>

$\frac{dP_i}{dt} = \frac{1}{C_n} \left( Q_i(t) - Q_{i+1}(t) \right)$ where, $C_n = \frac{C}{n_\text{comp}}$

Flow rate equation ($Q_i$): This governs how the flow in each compartment changes over time, depending on the pressures in the neighboring compartments and the resistance and inertance properties of each compartment.

$\frac{dQ_i}{dt} = \frac{1}{L_n} \left( P_i - P_{10} - R_n Q_i(t) \right)$, where $L_n = \frac{L}{n_\text{comp}}, \quad R_n = \frac{R}{n_\text{comp}}$

</details>


In [1]:
from autoemulate.core.compare import AutoEmulate
from autoemulate.core.sensitivity_analysis import SensitivityAnalysis
from autoemulate.simulations.flow_problem import FlowProblem
import warnings
warnings.filterwarnings("ignore")
figsize = (9, 5)

Set up the simulation parameters and ranges:


In [ ]:
parameters_range = {
    "T": (0.5, 2.0), # Cardiac cycle period (s)
    "td": (0.1, 0.5), # Pulse duration (s)
    "amp": (100.0, 1000.0), # Amplitude (e.g., pressure or flow rate)
    "dt": (0.0001, 0.01), # Time step (s)
    "C": (20.0, 60.0), # Compliance (unit varies based on context)
    "R": (0.01, 0.1), # Resistance (unit varies based on context)
    "L": (0.001, 0.005), # Inductance (unit varies based on context)
    "R_o": (0.01, 0.05), # Outflow resistance (unit varies based on context)
    "p_o": (5.0, 15.0) # Initial pressure (unit varies based on context)
}
output_names = ["pressure"]

simulator = FlowProblem(
    parameters_range=parameters_range,
    output_names=output_names,
    log_level="error"
)

Run the simulation for 100 sets of parameters sampled from the parameter space:


In [3]:
x = simulator.sample_inputs(100)
y = simulator.forward_batch(x)

Running simulations: 100%|██████████| 100/100 [00:43<00:00, 2.29sample/s] 


In [ ]:
print(x.shape, y.shape)

(torch.Size([100, 9]), torch.Size([100, 1]))

Use AutoEmulate to find the best emulator for this simulation:


In [ ]:
ae = AutoEmulate(x, y, models=["MLP", "GP"], log_level="error")  # remove models argument to use all models
best = ae.best_result()
print(best.model_name)

Comparing models: 100%|██████████| 2.00/2.00 [00:27<00:00, 13.6s/model]


'GaussianProcess'

### Sensitivity Analysis

1. Define the problem by creating a dictionary which contains the names and the boundaries of the parameters
2. Evaluate the contribution of each parameter via the Sobol and Morris methods.


In [ ]:
problem = {
    'num_vars': simulator.in_dim,
    'names': simulator.param_names,
    'bounds': simulator.param_bounds,
    'output_names': simulator.output_names,
}
sa = SensitivityAnalysis(best.model, problem=problem)

Sobol metrics:

- $S_1$: First-order sensitivity index.
- $S_2$: Second-order sensitivity index.
- $S_t$: Total sensitivity index.

Sobol interpretation:

- $S_1$ values sum to ≤ 1.0 (exact fraction of variance explained)
- $S_t - S_1$ = interaction effects involving that parameter
- Large $S_t - S_1$ gap indicates strong interactions


In [7]:
sobol_df = sa.run("sobol")
sobol_df

output   parameter index     value  confidence
0   pressure           T    S1  0.000437    0.000043
1   pressure          td    S1  0.021976    0.002809
2   pressure         amp    S1  0.936555    0.060176
3   pressure          dt    S1  0.000116    0.000015
4   pressure           C    S1  0.009577    0.001080
5   pressure           R    S1  0.044321    0.005678
6   pressure           L    S1  0.001985    0.000259
7   pressure         R_o    S1  0.000052    0.000008
8   pressure         p_o    S1  0.000032    0.000005
0   pressure           T    ST  0.000616    0.001663
1   pressure          td    ST  0.015703    0.012307
2   pressure         amp    ST  0.924193    0.072485
3   pressure          dt    ST -0.000365    0.000993
4   pressure           C    ST  0.007906    0.008801
5   pressure           R    ST  0.034223    0.016029
6   pressure           L    ST  0.000301    0.003803
7   pressure         R_o    ST -0.000068    0.000540
8   pressure         p_o    ST  0.001265    0.000468
0   pressure     (T, td)    S2 -0.000216    0.002614
1   pressure    (T, amp)    S2 -0.000329    0.003111
2   pressure     (T, dt)    S2 -0.000357    0.002616
3   pressure      (T, C)    S2 -0.000372    0.002652
4   pressure      (T, R)    S2 -0.000148    0.002636
5   pressure      (T, L)    S2 -0.000308    0.002605
6   pressure    (T, R_o)    S2 -0.000355    0.002617
7   pressure    (T, p_o)    S2 -0.000351    0.002618
8   pressure   (td, amp)    S2  0.005266    0.022373
9   pressure    (td, dt)    S2  0.000809    0.019804
10  pressure     (td, C)    S2  0.001538    0.019918
11  pressure     (td, R)    S2  0.002005    0.020754
12  pressure     (td, L)    S2  0.001063    0.019917
13  pressure   (td, R_o)    S2  0.000677    0.019819
14  pressure   (td, p_o)    S2  0.000703    0.019793
15  pressure   (amp, dt)    S2  0.000557    0.087541
16  pressure    (amp, C)    S2  0.000996    0.087812
17  pressure    (amp, R)    S2  0.007889    0.091299
18  pressure    (amp, L)    S2  0.001224    0.088571
19  pressure  (amp, R_o)    S2  0.000415    0.087703
20  pressure  (amp, p_o)    S2 -0.001042    0.087631
21  pressure     (dt, C)    S2  0.000524    0.001478
22  pressure     (dt, R)    S2  0.000602    0.001466
23  pressure     (dt, L)    S2  0.000553    0.001492
24  pressure   (dt, R_o)    S2  0.000555    0.001478
25  pressure   (dt, p_o)    S2  0.000555    0.001479
26  pressure      (C, R)    S2  0.000245    0.013327
27  pressure      (C, L)    S2  0.000192    0.012936
28  pressure    (C, R_o)    S2  0.000270    0.012969
29  pressure    (C, p_o)    S2  0.000204    0.012991
30  pressure      (R, L)    S2  0.002466    0.027028
31  pressure    (R, R_o)    S2  0.002283    0.027035
32  pressure    (R, p_o)    S2  0.002268    0.027100
33  pressure    (L, R_o)    S2  0.000085    0.005854
34  pressure    (L, p_o)    S2  0.000107    0.005861
35  pressure  (R_o, p_o)    S2  0.000113    0.000934

In [8]:
sa.plot_sobol(sobol_df, index="ST", figsize=figsize) 

Morris Interpretation:

- High $\mu^*$, Low $\sigma$: Important parameter with linear/monotonic effects
- High $\mu^*$, High $\sigma$: Important parameter with non-linear effects or interactions
- Low $\mu^*$, High $\sigma$: Parameter involved in interactions but not individually important
- Low $\mu^*$, Low $\sigma$: Unimportant parameter


In [9]:
morris_df = sa.run("morris")
morris_df

output parameter          mu     mu_star      sigma  mu_star_conf
0  pressure         T  -10.948407   10.971906   5.813799      0.310705
1  pressure        td   91.065063   95.507904  82.792793      5.130546
2  pressure       amp  702.636353  702.636353  86.185135      4.888344
3  pressure        dt   -5.425406    6.037108   5.297449      0.268716
4  pressure         C  -61.728821   61.743820  33.377426      1.968588
5  pressure         R -138.094833  138.094833  77.866798      4.937705
6  pressure         L    8.614614   27.807119  34.732384      1.330136
7  pressure       R_o   -3.789274    4.018043   3.009896      0.167161
8  pressure       p_o   -0.348657    3.154212   4.074439      0.149355

In [10]:
sa.plot_morris(morris_df, figsize=figsize)